In [3]:
#天网系统中记录DPS部分的测试。

import numpy as np
import pymysql
import configparser
import json
import time

In [26]:
ip = "139.199.102.41"
config = configparser.RawConfigParser()
config.readfp(open('../settings.cfg'))

dbname = config.get('jx3bla', 'username')
dbpwd = config.get('jx3bla', 'password')
db = pymysql.connect(ip,dbname,dbpwd,"jx3bla",port=3306,charset='utf8')
cursor = db.cursor()

d:\develop\python\python37\lib\site-packages\ipykernel_launcher.py:3: DeprecationWarning: This method will be removed in future versions.  Use 'parser.read_file()' instead.
  This is separate from the ipykernel package so we can avoid doing imports until


In [12]:
edition = "5.1.0"
mapdetail = "25人英雄达摩洞"

sql = """SELECT * FROM ActorStat WHERE edition>='%s' AND win=1"""%edition
cursor.execute(sql)
result = cursor.fetchall()

In [10]:
print(result[0:5])

(('乾坤一掷', '哑头陀', '2020-12-15', '484', '5.4.2', '003c9a9f17db7f6285649fe3ac757058', 1, "{'battleTime': 787, 'potList': [['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['齐光还是驱夷', '10d', 0, '哑头陀', '45s减疗叠加20层', ['不间断的减疗只计算一次']], ['帅卡卡', '23', 1, '哑头陀', '45s重伤，来源：罪业(78915

In [23]:
dpsAll = {"483": {}, "484": {}}

for rec in result:
    server = rec[0]
    boss = rec[1]
    map = rec[3]
    if map not in dpsAll:
        continue
    dpsMap = dpsAll[map]
    if boss not in dpsMap:
        dpsMap[boss] = {}
    dpsBoss = dpsMap[boss]
    if server not in dpsBoss:
        dpsBoss[server] = {}
    dpsServer = dpsBoss[server]
    
    stat = rec[7].replace("'",'"')
    Jstat = json.loads(stat)
    
    for line in Jstat["effectiveDPSList"]:
        player = line[0]
        occ = line[1]
        dps = int(line[2])
        if player not in dpsServer:
            dpsServer[player] = [dps, occ]
        else:
            if dps > dpsServer[player][0]:
                dpsServer[player] = [dps, occ]

In [ ]:
for map in dpsAll:
    mapName = {"483":"25人普通达摩洞", "484":"25人英雄达摩洞"}[map]
    for boss in dpsAll[map]:
        for server in dpsAll[map][boss]:
            for player in dpsAll[map][boss][server]:
                dps = dpsAll[map][boss][server][player][0]
                occ = dpsAll[map][boss][server][player][1]
                sql = """INSERT INTO HighestDps VALUES ("%s", "%s", "%s", "%s", "%s", %d)"""%(server, player, occ, mapName, boss, dps)
                cursor.execute(sql)
                
db.commit()

In [28]:
sql = """CREATE TABLE HighestDps(
         server VARCHAR(32),
         player VARCHAR(32),
         occ VARCHAR(32),
         map VARCHAR(32),
         boss VARCHAR(32),
         dps INT
         ) DEFAULT CHARSET utf8mb4"""
cursor.execute(sql)

0

In [32]:
#接下来测试从天网数据库中获取对应的角色。

server = "破阵子"
ids = "左渭雨@飞鸢泛月+唐郁+钟鸣"

ip = "139.199.102.41"
config = configparser.RawConfigParser()
config.readfp(open('../settings.cfg'))

dbname = config.get('jx3bla', 'username')
dbpwd = config.get('jx3bla', 'password')
db = pymysql.connect(ip,dbname,dbpwd,"jx3bla",port=3306,charset='utf8')
cursor = db.cursor()

playerDps = {}

ids_split = ids.split('+')
for id in ids_split:
    sql = '''SELECT occ, map, boss, dps from HighestDps WHERE server = "%s" and player = "%s"'''%(server, id)
    cursor.execute(sql)
    result = cursor.fetchall()
    playerDps[id] = {}
    for line in result:
        playerDps[id]["occ"] = line[0]
        if line[1] not in playerDps[id]:
            playerDps[id][line[1]] = [0, 0, 0, 0, 0, 0]
        if line[2] in ["余晖", "宓桃", "武雪散", "猿飞", "哑头陀", "岳琳&岳琅"]:
            bossNum = {"余晖": 0, "宓桃": 1, "武雪散": 2, "猿飞": 3, "哑头陀": 4, "岳琳&岳琅": 5}[line[2]]
            playerDps[id][line[1]][bossNum] = line[3]

db.close()




d:\develop\python\python37\lib\site-packages\ipykernel_launcher.py:8: DeprecationWarning: This method will be removed in future versions.  Use 'parser.read_file()' instead.
  


{'occ': '2h', '25人英雄达摩洞': [0, 388, 128, 298, 6, 9], '25人普通达摩洞': [6, 276, 0, 46412, 74, 0]}
{'occ': '7p', '25人英雄达摩洞': [197182, 162261, 123758, 140870, 5167199, 426512], '25人普通达摩洞': [211729, 172158, 172076, 122546, 159198, 104646]}
{'occ': '23', '25人英雄达摩洞': [242344, 183489, 148763, 229812, 114705, 181079], '25人普通达摩洞': [212191, 0, 201022, 137150, 181223, 154413]}


In [8]:

ip = "139.199.102.41"
config = configparser.RawConfigParser()
config.readfp(open('../settings.cfg'))

dbname = config.get('jx3bla', 'username')
dbpwd = config.get('jx3bla', 'password')
db = pymysql.connect(ip,dbname,dbpwd,"jx3bla",port=3306,charset='utf8')
cursor = db.cursor()

edition = "5.1.0"
mapdetail = "25人英雄达摩洞"

sql = """DROP TABLE IF EXISTS HighestDps"""
cursor.execute(sql)

sql = """CREATE TABLE HighestDps(
         server VARCHAR(32),
         player VARCHAR(32),
         occ VARCHAR(32),
         map VARCHAR(32),
         boss VARCHAR(32),
         dps INT
         ) DEFAULT CHARSET utf8mb4"""
cursor.execute(sql)

sql = """DROP TABLE IF EXISTS PotHistory"""
cursor.execute(sql)

sql = """CREATE TABLE PotHistory(
         server VARCHAR(32),
         player VARCHAR(32),
         occ VARCHAR(32),
         battleDate VARCHAR(32),
         map VARCHAR(32),
         boss VARCHAR(32),
         severe INT, 
         pot VARCHAR(64),
         ) DEFAULT CHARSET utf8mb4"""
cursor.execute(sql)

sql = """SELECT * FROM ActorStat WHERE edition>='%s' AND win=1"""%edition
cursor.execute(sql)
result = cursor.fetchall()

dpsAll = {"483": {}, "484": {}}
potAll = {"483": {}, "484": {}}

for rec in result:
    server = rec[0]
    boss = rec[1]
    battleDate = rec[2]
    map = rec[3]
    if map not in dpsAll:
        continue
    dpsMap = dpsAll[map]
    potMap = potAll[map]
    if boss not in dpsMap:
        dpsMap[boss] = {}
        potMap[boss] = {}
    dpsBoss = dpsMap[boss]
    potBoss = potMap[boss]
    if server not in dpsBoss:
        dpsBoss[server] = {}
        potBoss[server] = []
    dpsServer = dpsBoss[server]
    potServer = potBoss[server]

    stat = rec[7].replace("'",'"')
    Jstat = json.loads(stat)

    for line in Jstat["effectiveDPSList"]:
        player = line[0]
        occ = line[1]
        dps = int(line[2])
        if player not in dpsServer:
            dpsServer[player] = [dps, occ, 1]
        else:
            dpsServer[player][2] += 1
            if dps > dpsServer[player][0]:
                dpsServer[player][0] = dps
                dpsServer[player][1] = occ
                
    for line in Jstat["potList"]:
        player = line[0]
        occ = line[1]
        severe = line[2]
        pot = line[4]
        if "小药" not in pot:
            potServer.append([player, occ, severe, pot])

for map in dpsAll:
    mapName = {"483":"25人普通达摩洞", "484":"25人英雄达摩洞"}[map]
    for boss in dpsAll[map]:
        for server in dpsAll[map][boss]:
            for player in dpsAll[map][boss][server]:
                dps = dpsAll[map][boss][server][player][0]
                occ = dpsAll[map][boss][server][player][1]
                num = dpsAll[map][boss][server][player][2]
                #print(server, player, occ, mapName, boss, dps, num)
                sql = """INSERT INTO HighestDps VALUES ("%s", "%s", "%s", "%s", "%s", %d, %d)"""%(server, player, occ, mapName, boss, num, dps)
                cursor.execute(sql)

for map in potAll:
    mapName = {"483":"25人普通达摩洞", "484":"25人英雄达摩洞"}[map]
    for boss in potAll[map]:
        for server in potAll[map][boss]:
            for line in potAll[map][boss][server]:
                player = line[0]
                occ = line[1]
                severe = line[2]
                pot = line[3]
                sql = """INSERT INTO PotHistory VALUES ("%s", "%s", "%s", "%s", "%s", "%s", %d, "%s")"""%(server, player, occ, battleDate, mapName, boss, severe, pot)
                cursor.execute(sql)
            
db.commit()
    


d:\develop\python\python37\lib\site-packages\ipykernel_launcher.py:3: DeprecationWarning: This method will be removed in future versions.  Use 'parser.read_file()' instead.
  This is separate from the ipykernel package so we can avoid doing imports until


梦江南 糖依糖 5h 25人普通达摩洞 哑头陀 1 38s重伤，来源：净天眼(84577)
梦江南 上已 4m 25人普通达摩洞 哑头陀 1 38s重伤，来源：净天眼(86438)
梦江南 芳菲阑珊 4m 25人普通达摩洞 哑头陀 1 7m8s重伤，来源：热浪(78572)
梦江南 途人 7p 25人普通达摩洞 哑头陀 1 7m8s重伤，来源：未知
梦江南 完蛋惹@长安城 6d 25人普通达摩洞 哑头陀 1 7m15s重伤，来源：热浪(82500)
梦江南 灯等等灯灯 211 25人普通达摩洞 哑头陀 1 7m15s重伤，来源：热浪(82500)
梦江南 一花以墨一 5d 25人普通达摩洞 哑头陀 1 7m15s重伤，来源：热浪(82500)
梦江南 糖依糖 5h 25人普通达摩洞 哑头陀 1 7m16s重伤，来源：罪业(63049)
梦江南 书小茶 2h 25人普通达摩洞 哑头陀 1 7m20s重伤，来源：未知
梦江南 菊花的春天@隐士 6 25人普通达摩洞 哑头陀 0 承伤逃课，次数：2
梦江南 谣哥 6 25人普通达摩洞 哑头陀 0 承伤逃课，次数：3
梦江南 糖小策 3 25人普通达摩洞 哑头陀 0 承伤逃课，次数：2
梦江南 茶咕 22 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 芽音 6 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 海鲜芝士浓卷 21 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 祁依 6 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 小月亮守护 7 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 书小茶 2 25人普通达摩洞 哑头陀 0 承伤逃课，次数：2
梦江南 精神科主任 5 25人普通达摩洞 哑头陀 0 承伤逃课，次数：3
梦江南 完蛋惹@长安城 6 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 尼茶得太深@隐士 1 25人普通达摩洞 哑头陀 3 控制戏龙珠，次数：12
梦江南 没见过靓仔嘛 3d 25人普通达摩洞 哑头陀 3 团队-心法DPS达到补贴线(133%/120%)
梦江南 小月亮守护 7p 25人普通达摩洞 哑头陀 0 团队-心法DPS低于预警线(79%/85%)
梦江南 芳菲阑珊 4m 25人普通达摩洞 哑头陀 3 团队-心法DPS达到补贴线(

梦江南 时******* 10d 25人普通达摩洞 哑头陀 3 团队-心法DPS达到补贴线(127%/120%)
梦江南 白** 22h 25人普通达摩洞 哑头陀 0 团队-心法DPS低于预警线(81%/85%)
梦江南 唐** 7p 25人普通达摩洞 哑头陀 0 团队-心法DPS低于预警线(78%/85%)
梦江南 别** 1d 25人普通达摩洞 哑头陀 3 团队-心法DPS达到补贴线(244%/120%)
梦江南 幽*** 10t 25人普通达摩洞 哑头陀 3 团队-心法DPS达到补贴线(142%/120%)
梦江南 帅气的丐 9 25人普通达摩洞 哑头陀 1 4m9s重伤，来源：净天眼(62980)
梦江南 可达吖 3d 25人普通达摩洞 哑头陀 0 4m9s减疗叠加20层
梦江南 可达吖 3d 25人普通达摩洞 哑头陀 1 4m11s重伤，来源：定波(14220)
梦江南 搞乜鬼啊 6h 25人普通达摩洞 哑头陀 1 7m21s重伤，来源：未知
梦江南 皑皑袖上雪 5d 25人普通达摩洞 哑头陀 1 7m35s重伤，来源：热浪(68750)
梦江南 丁少离 7p 25人普通达摩洞 哑头陀 1 7m39s重伤，来源：未知
梦江南 小啵公主 2d 25人普通达摩洞 哑头陀 1 7m40s重伤，来源：未知
梦江南 落星痕 7p 25人普通达摩洞 哑头陀 1 7m43s重伤，来源：未知
梦江南 断魂刺不中 5h 25人普通达摩洞 哑头陀 1 7m43s重伤，来源：未知
梦江南 断魂刺不中 5 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 夏欢欢 6 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 落星痕 7 25人普通达摩洞 哑头陀 0 承伤逃课，次数：3
梦江南 皑皑袖上雪 5 25人普通达摩洞 哑头陀 0 承伤逃课，次数：2
梦江南 执子手 1 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 小啵公主 2 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 奶鸽油炸好吃 22 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 丁少离 7 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 樱花莓莓冰 10 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 紫藤凛花 21 25人普通达摩洞 哑头陀 0 承

梦江南 不许吃手手 6d 25人普通达摩洞 哑头陀 1 团队-心法DPS未到及格线(73%/75%)
梦江南 小伞伞儿 24 25人普通达摩洞 哑头陀 1 团队-心法DPS未到及格线(72%/75%)
梦江南 百酱 6d 25人普通达摩洞 哑头陀 0 团队-心法DPS低于预警线(78%/85%)
梦江南 牟筱筱 6d 25人普通达摩洞 哑头陀 0 团队-心法DPS低于预警线(84%/85%)
梦江南 一辟衍一 211 25人普通达摩洞 哑头陀 0 团队-心法DPS低于预警线(82%/85%)
梦江南 樱桃小橘子 3d 25人普通达摩洞 哑头陀 3 团队-心法DPS达到补贴线(130%/120%)
梦江南 李小狼 3d 25人普通达摩洞 哑头陀 3 团队-心法DPS达到补贴线(139%/120%)
梦江南 辞凉亦暖 4p 25人普通达摩洞 哑头陀 0 提前开怪：生太极
梦江南 巷宫 6h 25人普通达摩洞 哑头陀 1 3m14s重伤，来源：龙气(51180)
梦江南 杨柳 7p 25人普通达摩洞 哑头陀 1 5m3s重伤，来源：热浪(50000)
梦江南 曲一夏 6d 25人普通达摩洞 哑头陀 1 5m5s重伤，来源：未知
梦江南 君诺 8 25人普通达摩洞 哑头陀 1 5m26s重伤，来源：未知
梦江南 骗归归的钱 5 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 四二带俩王 3 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 茉沏三分糖 2 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 任卿若月飞 4 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 伍陌城 21 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 半闲赋 21 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 蚩黎 6 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 吱吱复织织 2 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 唐门天花板 7 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 蝶崽 6 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 秋宝宝 5 25人普通达摩洞 哑头陀 3 控制戏龙珠，次数：10
梦江南 吱吱复织织 2d 25人普通达摩洞 哑头陀 0 团队-心法DPS低于预警线(82

梦江南 岁将寒 211 25人普通达摩洞 哑头陀 1 团队-心法DPS未到及格线(74%/75%)
梦江南 细眉 21t 25人普通达摩洞 哑头陀 3 团队-心法DPS达到补贴线(233%/120%)
梦江南 你是月色真美 21d 25人普通达摩洞 哑头陀 0 提前开怪：盾猛(推测)
梦江南 葑羞羞 10 25人普通达摩洞 哑头陀 1 3s重伤，来源：罪业(11722)
梦江南 胸平浪静 7 25人普通达摩洞 哑头陀 1 4s重伤，来源：罪业(78451)
梦江南 本月花呗账单 10 25人普通达摩洞 哑头陀 0 承伤逃课，次数：2
梦江南 沙一汀 5 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 你是月色真美 21 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 扰弦 1 25人普通达摩洞 哑头陀 0 承伤逃课，次数：2
梦江南 陆渝渝 10 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 琅宴 7 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 三杯罚酒 2 25人普通达摩洞 哑头陀 0 承伤逃课，次数：1
梦江南 叶心渡 8 25人普通达摩洞 哑头陀 0 承伤逃课，次数：2
梦江南 鹤皈 22 25人普通达摩洞 哑头陀 0 承伤逃课，次数：2
梦江南 扰弦 1 25人普通达摩洞 哑头陀 3 控制戏龙珠，次数：9
梦江南 逄决 23 25人普通达摩洞 哑头陀 3 团队-心法DPS达到补贴线(120%/120%)
梦江南 车辙 3t 25人普通达摩洞 哑头陀 3 团队-心法DPS达到补贴线(229%/120%)
梦江南 筱玖玖 5d 25人普通达摩洞 哑头陀 0 团队-心法DPS低于预警线(77%/85%)
梦江南 冇衍员 211 25人普通达摩洞 哑头陀 0 团队-心法DPS低于预警线(80%/85%)
梦江南 你是月色真美 21d 25人普通达摩洞 哑头陀 3 团队-心法DPS达到补贴线(127%/120%)
梦江南 忘崽 3d 25人普通达摩洞 哑头陀 1 1m48s重伤，来源：净天眼(91339)
梦江南 洪兴社十三妹 3d 25人普通达摩洞 哑头陀 1 4m20s重伤，来源：落剑(72667)
梦江南 洪兴社十三妹 3d 25人普通达摩洞 哑头陀 0 4m59s重伤，来源：杯水留影
梦江南 清清清风 6d 25人

...

梦江南 给我个枕头 211 25人英雄达摩洞 武雪散 0 7m11s重伤，来源：杯水留影
梦江南 心境@唯我独尊 23 25人英雄达摩洞 武雪散 1 7m35s重伤，来源：穿脊牵肌·撕裂(43747)
梦江南 山*** 4m 25人英雄达摩洞 武雪散 1 3m49s重伤，来源：百邪癫狂(6932587)
梦江南 藏***** 25 25人英雄达摩洞 武雪散 1 6m8s重伤，来源：穿脊牵肌·撕裂(34274)
梦江南 山*** 4m 25人英雄达摩洞 武雪散 1 6m17s重伤，来源：穿脊牵肌·撕裂(11651)
梦江南 暮** 6d 25人英雄达摩洞 武雪散 1 7m2s重伤，来源：戮·白霜落(114245)
梦江南 山*** 4m 25人英雄达摩洞 武雪散 0 7m8s重伤，来源：杯水留影
梦江南 藏***** 25 25人英雄达摩洞 武雪散 0 7m15s重伤，来源：杯水留影
梦江南 青**** 6d 25人英雄达摩洞 武雪散 0 提前开怪：献祭毒爆
梦江南 唐** 7p 25人英雄达摩洞 武雪散 1 1m31s重伤，来源：百邪癫狂(6932587)
梦江南 青**** 6d 25人英雄达摩洞 武雪散 0 提前开怪：献祭毒爆
梦江南 唐** 7p 25人英雄达摩洞 武雪散 1 1m31s重伤，来源：百邪癫狂(6932587)
梦江南 快乐挽月月 8 25人英雄达摩洞 武雪散 1 10s重伤，来源：罗织针·挽花(128181)
梦江南 舟颜颜 5d 25人英雄达摩洞 武雪散 1 7m7s重伤，来源：未知
梦江南 夏茶 211 25人英雄达摩洞 武雪散 1 7m7s重伤，来源：未知
梦江南 式霖 6d 25人英雄达摩洞 武雪散 1 7m7s重伤，来源：未知
梦江南 北朽独木 7p 25人英雄达摩洞 武雪散 1 7m7s重伤，来源：未知
梦江南 孙夭夭@剑胆琴心 7p 25人英雄达摩洞 武雪散 1 7m7s重伤，来源：未知
梦江南 蛊煌煌 6d 25人英雄达摩洞 武雪散 1 7m7s重伤，来源：未知
梦江南 闻兮 6d 25人英雄达摩洞 武雪散 1 7m7s重伤，来源：未知
梦江南 秋灵韵 6h 25人英雄达摩洞 武雪散 1 7m7s重伤，来源：未知
梦江南 淮吾吾 6d 25人英雄达摩洞 武雪散 1 7m7s重伤，来源：未知
梦江南 唐小起 7p 25人英雄达摩洞

梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 玛***** 6d 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 哥***** 211 25人英雄达摩洞 武雪散 1 1m47s重伤，来源：百邪癫狂(6932587)
梦江南 小** 2d 25人英雄达摩洞 武雪散 1 2m21s重伤，来源：未知
梦江南 我**** 6d 25人英雄达摩洞 武雪散 1 3m57s重伤，来源：百邪癫狂(6932587)
梦江南 江*** 8 25人英雄达摩洞 武雪散 1 3m57s重伤，来源：百邪癫狂(6932587)
梦江南 江*** 8 25人英雄达摩洞 武雪散 0 4m37s重伤，来源：杯水留影
梦江南 啤***** 3d 25人英雄达摩洞 武雪散 1 4m42s重伤，来源：未知
梦江南 我**** 6d 25人英雄达摩洞 武雪散 0 4m44s重伤，来源：杯水留影
梦江南 小** 2d 25人英雄达摩洞 武雪散 1 7m20s重伤，来源：戮·白霜落(101291)
梦江南 铁锹战神 3t 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 铁锹战神 3t 25人

梦江南 半阙凉音弦 4m 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 半阙凉音弦 4m 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 半阙凉音弦 4m 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 半阙凉音弦 4m 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 半阙凉音弦 4m 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 半阙凉音弦 4m 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 半阙凉音弦 4m 25人英雄达摩洞 武雪散 0 小药数量错误：0
梦江南 专业小逗比 1d 25人英雄达摩洞 武雪散 1 1m47s重伤，来源：百邪癫狂(6932587)
梦江南 冬宵淡酒 5d 25人英雄达摩洞 武雪散 1 3m57s重伤，来源：百邪癫狂(6932587)
梦江南 刺蘑菇 22h 25人英雄达摩洞 武雪散 1 6m24s重伤，来源：穿脊牵肌·撕裂(55242)
梦江南 青雀咕咕@天鹅坪 22d 25人英雄达摩洞 武雪散 1 7m11s重伤，来源：戮·挽花(177165)
梦江南 好无聊的名字 3d 25人英雄达摩洞 武雪散 1 7m16s重伤，来源：戮·白霜落(129399)
梦江南 拜托了 24 25人英雄达摩洞 武雪散 1 7m16s重伤，来源：戮·白霜落(112599)
梦江南 剑去去 8 25人英雄达摩洞 武雪散 1 3m49s重伤，来源：百邪癫狂(6932587)
梦江南 玛丽苏文男主 22d 25人英雄达摩洞 武雪散 1 3m49s重伤，来源：百邪癫狂(6932587)
梦江南 剑去去 8 25人英雄达摩洞 武雪散 0 4m37s重伤，来源：杯水留影
梦江南 陆仔也 25 25人英雄达摩洞 武雪散 1 6m4s重伤，来源：穿脊牵肌·撕裂(32634)
梦江南 我是你谷歌 10t 25人英雄达摩洞 武雪散 1 6m21s重伤，来源：穿针(127404)
梦江南 伏晨初 24 25人英雄达摩洞 武雪散 1 1m47s重伤，来源：百邪癫狂(6932587)
梦江南 在你容颜搁浅 4m 25人英雄达摩洞 武雪散 1 2m10s重伤，来源：罗织针·断脉(79465)
梦江南 须鱼鱼 5d 25人英雄达摩洞 武雪散 1 1m47s重伤，来源：百邪癫狂(6932587)
梦江南 我怎么被秒了 2h 25人英

绝代天骄 眼下皆栖洛 7p 25人英雄达摩洞 武雪散 0 3m46s重伤，来源：杯水留影
绝代天骄 幸慕 25 25人英雄达摩洞 武雪散 1 3m53s重伤，来源：散魂(53755)
绝代天骄 一士多啤梨一 4p 25人英雄达摩洞 武雪散 1 4m4s重伤，来源：罗织针·断脉(87082)
绝代天骄 情已 22h 25人英雄达摩洞 武雪散 1 6m37s重伤，来源：穿脊牵肌·撕裂(112729)
绝代天骄 情已 22h 25人英雄达摩洞 武雪散 0 7m13s重伤，来源：杯水留影
绝代天骄 眼下皆栖洛 7p 25人英雄达摩洞 武雪散 1 7m18s重伤，来源：戮·白霜落(115636)
绝代天骄 气质质 2d 25人英雄达摩洞 武雪散 1 2m33s重伤，来源：银丝千织(68250)
绝代天骄 雨落兰亭 3d 25人英雄达摩洞 武雪散 1 6m17s重伤，来源：穿脊牵肌·撕裂(28508)
绝代天骄 雨落兰亭 3d 25人英雄达摩洞 武雪散 1 6m37s重伤，来源：未知
绝代天骄 我不是藏剑@亢龙有悔 4m 25人英雄达摩洞 武雪散 1 1m47s重伤，来源：百邪癫狂(6932587)
绝代天骄 这个名起的好 21d 25人英雄达摩洞 武雪散 1 2m45s重伤，来源：银丝千织(70916)
绝代天骄 叶寻羽 2h 25人英雄达摩洞 武雪散 1 2m45s重伤，来源：银丝千织(68392)
绝代天骄 叶寻羽 2h 25人英雄达摩洞 武雪散 0 3m31s重伤，来源：杯水留影
绝代天骄 一李有病一 4p 25人英雄达摩洞 武雪散 1 3m57s重伤，来源：百邪癫狂(6932587)
绝代天骄 血色琉璃树 4p 25人英雄达摩洞 武雪散 1 4m43s重伤，来源：未知
绝代天骄 酸伞伞 24 25人英雄达摩洞 武雪散 1 6m34s重伤，来源：穿脊牵肌·撕裂(88686)
绝代天骄 冬马家的十六 3t 25人英雄达摩洞 武雪散 1 6m45s重伤，来源：穿针(126109)
绝代天骄 冬马家的十六 3t 25人英雄达摩洞 武雪散 0 7m21s重伤，来源：杯水留影
绝代天骄 冬马家的十六 3t 25人英雄达摩洞 武雪散 3 团队-心法DPS达到补贴线(143%/120%)
绝代天骄 这个名起的好 21d 25人英雄达摩洞 武雪散 1 团队-心法DPS未到及格线(32%

幽月轮 砸琴不打脸 22h 25人英雄达摩洞 武雪散 1 2m57s重伤，来源：银丝千织(82433)
幽月轮 曲芮芮 6d 25人英雄达摩洞 武雪散 1 4m20s重伤，来源：散魂(52804)
幽月轮 白夜流萤 24 25人英雄达摩洞 武雪散 1 6m1s重伤，来源：罗织针·断脉(59425)
幽月轮 白夜流萤 24 25人英雄达摩洞 武雪散 1 6m41s重伤，来源：未知
幽月轮 曲芮芮 6d 25人英雄达摩洞 武雪散 1 6m56s重伤，来源：穿脊牵肌·撕裂(64100)
幽月轮 云一 4p 25人英雄达摩洞 武雪散 1 7m45s重伤，来源：戮·白霜落(119011)
幽月轮 砸琴不打脸 22h 25人英雄达摩洞 武雪散 1 7m45s重伤，来源：戮·白霜落(120000)
幽月轮 糖瑭 7p 25人英雄达摩洞 武雪散 1 7m45s重伤，来源：戮·白霜落(119011)
幽月轮 茶绵绵 2d 25人英雄达摩洞 武雪散 1 2m44s重伤，来源：银丝千织(79009)
幽月轮 小孙@隐士 2d 25人英雄达摩洞 武雪散 1 3m59s重伤，来源：百邪癫狂(6932587)
幽月轮 仙丹 4m 25人英雄达摩洞 武雪散 1 3m59s重伤，来源：百邪癫狂(6932587)
幽月轮 小孙@隐士 2d 25人英雄达摩洞 武雪散 0 4m48s重伤，来源：杯水留影
幽月轮 白居@梦江南 22d 25人英雄达摩洞 武雪散 1 6m16s重伤，来源：穿脊牵肌·撕裂(13506)
幽月轮 妙玄 7 25人英雄达摩洞 武雪散 1 6m17s重伤，来源：穿脊牵肌·撕裂(75422)
幽月轮 萝矶 22h 25人英雄达摩洞 武雪散 1 6m52s重伤，来源：穿脊牵肌·撕裂(148646)
幽月轮 让小三先走 4p 25人英雄达摩洞 武雪散 1 6m53s重伤，来源：穿脊牵肌·撕裂(61280)
幽月轮 白居@梦江南 22d 25人英雄达摩洞 武雪散 0 7m25s重伤，来源：杯水留影
幽月轮 萝矶 22h 25人英雄达摩洞 武雪散 0 7m32s重伤，来源：杯水留影
幽月轮 让小三先走 4p 25人英雄达摩洞 武雪散 0 7m36s重伤，来源：杯水留影
幽月轮 妙玄 7 25人英雄达摩洞 武雪散 0 7m59s重伤，来源：杯水留影
幽月轮 茶绵绵 2d 25人英雄达摩洞 武雪

In [6]:
print(result[0])

('乾坤一掷', '哑头陀', '2020-12-15', '484', '5.4.2', '003c9a9f17db7f6285649fe3ac757058', 1, "{'battleTime': 787, 'potList': [['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['欧欧欧欧小月', '10t', 0, '哑头陀', '小药数量错误：0'], ['齐光还是驱夷', '10d', 0, '哑头陀', '45s减疗叠加20层', ['不间断的减疗只计算一次']], ['帅卡卡', '23', 1, '哑头陀', '45s重伤，来源：罪业(78915)